# Day 13, Step-wise execution on an ASCII map

* [Day 13](https://adventofcode.com/2018/day/13)

We've seen a similar problem [last year](../2017/Day%2019.ipynb), where we had to intrepret an ASCII map of the problem. I see no reason not to follow the same approach here.

We

1. 'read' the map to find all carts, noting their positions. Since they are always located on a straight section (`-` or `|`) we can trivially 'repair' the map at that point. (0, 0) is the top left.
2. Move the carts in (y, x) priority order (top to bottom, and per row, from left to right), checking for collisions.
3. Track last intersection rotation per cart, so we can rotate them correctly when coming to an intersection.

## Part 2

Part two is added in-line to remove the carts that collided; with the set-up for part 1 this was easy to add.

In [1]:
import re

from dataclasses import dataclass, field
from enum import Enum
from itertools import count
from typing import Optional, Sequence, Set, Tuple

class Direction(Enum):
    up = '^', -1, 0, 'left', 'right'
    down = 'v', 1, 0, 'right', 'left'
    left = '<', 0, -1, 'down', 'up'
    right = '>', 0, 1, 'up', 'down'
    
    def __new__(cls, char: str, dy: int, dx: int, left: str, right: str) -> None:
        instance = object.__new__(cls)
        instance._value_ = char
        instance.dy = dy
        instance.dx = dx
        instance._turns = {'left': left, 'right': right}
        return instance
    
    def make_turn(self, move: 'Move') -> 'Direction':
        turn = self._turns.get(move.name, self.name)
        return type(self)[turn]

class Move(Enum):
    left = 0
    straight = 1
    right = 2
    
    @property
    def next(self) -> 'Move':
        enum = type(self)
        return enum((self.value + 1) % len(enum))

@dataclass(frozen=True, order=True)
class Cart:
    # order matters here; y must be compared before x
    y: int
    x: int
    direction: Direction = field(compare=False)
    last_intersection_move: Move = field(
        default=Move.right, compare=False)
    id: int = field(default_factory=count().__next__, compare=False)

    @property
    def pos(self) -> Tuple[int, int]:
        return self.y, self.x
    
    @property
    def next_pos(self) -> Tuple[int, int]:
        return (self.y + self.direction.dy, self.x + self.direction.dx)
    
    def move(self, next_map_char: str) -> 'Cart':
        y, x = self.next_pos
        direction = self.direction
        last_move = self.last_intersection_move
        if next_map_char == '+':
            last_move = last_move.next
            direction = direction.make_turn(last_move)
        elif next_map_char == '\\':
            if direction in (Direction.up, Direction.down):
                turn = Move.left
            else:
                turn = Move.right
            direction = direction.make_turn(turn)
        elif next_map_char == '/':
            if direction in (Direction.up, Direction.down):
                turn = Move.right
            else:
                turn = Move.left
            direction = direction.make_turn(turn)
        return type(self)(y, x, direction, last_move, id=self.id)

class Tracks:
    def __init__(self, trackmap: Sequence[str], carts: Set[Cart]):
        self.trackmap = trackmap
        self.start_state = self.carts = carts
    
    @classmethod
    def from_raw_map(cls, map: str):
        lines = map.splitlines()
        cleaned = []
        carts = set()
        for y, line in enumerate(lines):
            for m in re.finditer(r'[<^>v]', line):
                direction = Direction(m[0])
                x = m.start()
                if direction.name in ('up', 'down'):
                    section = '|'
                else:
                    section = '-'
                line = f"{line[:x]}{section}{line[x + 1:]}"
                carts.add(Cart(y, x, direction))
            cleaned.append(line)
        return cls(cleaned, carts)

    def reset(self):
        self.carts = self.start_state
        
    def __str__(self):
        lines = [list(l) for l in self.trackmap]
        for cart in self.carts:
            lines[cart.y][cart.x] = cart.direction.value
        return '\n'.join([''.join(l) for l in lines])
    
    def step(self, remove_collided: bool = False) -> Optional[Tuple[int, int]]:
        new_state = set(self.carts)
        for cart in sorted(self.carts):
            try:
                new_state.remove(cart)
            except KeyError:
                # cart was removed due to a collision
                continue
            ny, nx = cart.next_pos
            cart = cart.move(self.trackmap[ny][nx])
            if cart in new_state:
                # collision!
                if not remove_collided:
                    return cart.pos
                new_state.remove(cart)
                continue
            new_state.add(cart)
        self.carts = new_state
    
    def run_carts(self, remove_collided: bool = False) -> Tuple[int, int]:
        while True:
            pos = self.step(remove_collided)
            if pos is not None:
                self.reset()
                return pos[::-1]
            if len(self.carts) == 1:
                # last cart standing
                cart, = self.carts
                self.reset()
                return cart.pos[::-1]

In [2]:
testtracks = Tracks.from_raw_map(r'''
/->-\        
|   |  /----\ 
| /-+--+-\  |
| | |  | v  |
\-+-/  \-+--/
  \------/  '''[1:])
assert testtracks.run_carts() == (7, 3)

In [3]:
import aocd

data = aocd.get_data(day=13, year=2018)
tracks = Tracks.from_raw_map(data)

In [4]:
print('Part 1:', ','.join(map(str, tracks.run_carts())))

Part 1: 71,121


In [5]:
test2tracks = Tracks.from_raw_map(r'''
/>-<\  
|   |  
| /<+-\ 
| | | v
\>+</ |
  |   ^
  \<->/'''[1:])
assert test2tracks.run_carts(True) == (6, 4)

In [6]:
print('Part 2:', ','.join(map(str, tracks.run_carts(True))))

Part 2: 71,76


The animation produced below can be viewed online [via the Jupyter notebook viewer](https://nbviewer.jupyter.org/github/mjpieters/adventofcode/blob/master/2018/Day%2013.ipynb); the GitHub renderer filters the video out.

In [7]:
%matplotlib inline
from datetime import datetime, timedelta
from collections import deque
import ipywidgets as widgets
import matplotlib.patches as mpatch
import matplotlib.pyplot as plt
from matplotlib import animation
from IPython.display import display
from PIL import Image

plt.rc('animation', html='html5')

tiles = {
    "+": (0b00100, 0b00100, 0b11111, 0b00100, 0b00100),
    "|": (0b00100, 0b00100, 0b00100, 0b00100, 0b00100),
    "-": (0b00000, 0b00000, 0b11111, 0b00000, 0b00000),
    "/": (0b00000, 0b00010, 0b00100, 0b01000, 0b00000),
    "\\": (0b00000, 0b01000, 0b00100, 0b00010, 0b00000),
}
tiles = {
    k: Image.frombytes(
        '1', (5, 5), bytes([b << 3 for b in v])
    ).convert('RGB').point(lambda v: 255 if not v else 75)
    for k, v in tiles.items()
}

def _track_image(tracks):
    trackmap = tracks.trackmap
    height = len(trackmap)
    width = max(len(l.rstrip()) for l in trackmap)
    img = Image.new('RGB', (width * 5, height * 5), 'white')
    for y, line in enumerate(trackmap):
        for x, char in enumerate(line):
            if char in tiles:
                img.paste(tiles[char], (x * 5, y * 5))
    return img

def _gen_frames(tracks):
    frames = []
    while True:
        tracks.step(True)
        frames.append(set(tracks.carts))
        if len(tracks.carts) == 1:
            break
    tracks.reset()
    return frames

def animate(tracks):
    frames = _gen_frames(tracks)
    frames.append(None)
    carts = {c.id: c for c in frames[0]}
    
    progress = widgets.IntProgress(
        value=0,
        min=0,
        max=len(frames),
        step=1,
        description='Rendering:',
        bar_style='info',
        orientation='horizontal'
    )
    class ETA:
        """Rough and ready exponential moving average estimated time of completion"""
        def __init__(self, total, progress):
            self.total = total
            self.started = self.last = self.last_update = datetime.now()
            self.current_estimate = timedelta(0)
            self.window = 1000
            self.samples = deque(maxlen=self.window * 2)
            
            self.widget = widgets.Label(value="  0.0%")
            progress.observe(self.update_eta, names='value')            
    
        @property
        def ema(self):
            current_ema = 0
            for _ in range(max(len(self.samples) - self.window, 0)):
                current_ema += self.samples[0]
                self.samples.rotate(-1)
            current_ema /= self.window
            c = 2.0 / (self.window + 1)
            for _ in range(min(len(self.samples), self.window)):
                current_ema = (c * self.samples[0]) + ((1 - c) * current_ema)
                self.samples.rotate(-1)
            return current_ema

        def update_eta(self, change):
            count = change['new']
            progress = count / self.total
            now = datetime.now()
            time_taken, self.last = (now - self.last).total_seconds(), now
            self.samples.append(time_taken)
            if now - self.last_update >= timedelta(seconds=1):
                # update the ETA roughly once a second
                self.last_update = now
                remainder = self.total - count
                self.current_estimate = timedelta(seconds=int(self.ema * remainder))
            est = ""
            if self.current_estimate:
                est = f" ETA {self.current_estimate}"
            self.widget.value = f"{progress:5.2%}{est}"

    progress_widget = widgets.HBox([progress, ETA(len(frames), progress).widget])
    display(progress_widget)
    
    fig, ax = plt.subplots(figsize=(12,12))
    fig.subplots_adjust(left=0, bottom=0, right=1, top=1, wspace=0, hspace=0)
    ax.set_axis_off()
    ax.imshow(_track_image(tracks), zorder=0, interpolation='bilinear')
    plt.close(fig)

    translate = lambda y, x: (x * 5 + 2, y * 5 + 1)

    cm = plt.get_cmap('brg')
    colours = cm._resample(len(carts))(range(len(carts)))
    
    cart_artists = {}
    for (cartid, cart), c in zip(sorted(carts.items()), colours):
        circle = mpatch.Circle(translate(*cart.pos), 2, color=c, animated=True)
        cart_artists[cartid] = circle
        ax.add_artist(circle)
    
    collisions = set()

    def render(active_carts):
        if active_carts is None:
            # end frames marker
            progress.close()
            progress_widget.layout.display = 'none'
            return ()

        updated = []
        collided = carts.copy()

        # process carts that are still running
        for cart in active_carts:
            circle = cart_artists[cart.id]
            circle.set_center(translate(*cart.pos))
            updated.append(circle)
            del collided[cart.id]
            carts[cart.id] = cart

        for cart in sorted(collided.values()):
            del carts[cart.id]
            circle = cart_artists.pop(cart.id)
            circle.remove()

            old_pos, new_pos = cart.pos, cart.next_pos
            if not collisions.isdisjoint({old_pos, new_pos}):
                continue
            collisions.update({old_pos, new_pos})

            collision = mpatch.Rectangle(
                circle.get_center(), 3, 3, 45,
                color="red", animated=True)
            ax.add_artist(collision)
            updated.append(collision)

        progress.value += 1
        return updated 
    
    return animation.FuncAnimation(
        fig, render, frames=frames,
        interval=11, blit=True, repeat_delay=5000
    )

animate(tracks)